# Convert .Rmd to .ipynb


In [1]:
# install.packages("devtools")
# remove.packages("rlang")
# install.packages("rlang")
# devtools::install_github("mkearney/rmd2jupyter")
# install.packages("rmd2jupyter")
# library("rmd2jupyter")

In [2]:
# rmd to ipynb
# rmd2jupyter("Preprocessing Data for Meta-Analyses.Rmd")

In [3]:
# install.packages("rmarkdown")

# Preprocess data of raw covidence Export



In [4]:
raw.df <- read.csv("final_data_export.csv")


## Install and load Dplyr


In [5]:
# install.packages("dplyr")
library("dplyr")
# install.packages("sjmisc")
library("sjmisc")
# for data manipulation with dplyr see: https://www.youtube.com/watch?v=Gvhkp-Yw65U
# for splitting 2 values in 1 cell see: https://www.youtube.com/watch?v=DiY8EqZDwoI at 3:17 (e.g. if 2 scales for 1 outcome)
# for joining 2 data frames see:        https://www.youtube.com/watch?v=DiY8EqZDwoI at 11:57


Attache Paket: 'dplyr'


Die folgenden Objekte sind maskiert von 'package:stats':

    filter, lag


Die folgenden Objekte sind maskiert von 'package:base':

    intersect, setdiff, setequal, union


Warning message:
"Paket 'sjmisc' wurde unter R Version 4.2.1 erstellt"


In [6]:
my.raw.df <- raw.df %>%
  filter(Reviewer.Name == "Robin Jacob", Study.design == "Passive RCT")

## Drop unimportant columns by name

### Remove column rages (first columns)

In [7]:
my.df <- my.raw.df %>%
  select(-Reviewer.Name:-Further.Information.inserted.in.Extraction.Form.)  # "-" indicates deleting these columns

In [28]:
# set options to print entire df (extend max. rows end cols)
options(repr.matrix.max.rows=30, repr.matrix.max.cols=1100)

In [29]:
my.df

Covidence.. Study.ID                
1  4325        Ratanasiripong 2015     
2  4178        Sloan 2016              
3  3762        Nidich 2009             
4  3760        Barry 2019              
5  3759        Chen 2013               
6  3736        Warnecke 2011           
7  2925        Johnson-Waddell 2018    
8  2864        Plummer 2018            
9  2574        Janowiak 1994           
10 2416        Oman 2007               
11 2267        Weytens 2014            
12 2201        Bonamo 2015             
13 2075        Smith 2021              
14 1897        Wang 2021               
15 1889        Fish 2019               
16 1737        Siembor 2018            
17 1582        Lee 2018                
18 1574        Bultas 2021             
19 1469        Huberty 2019            
20 1416        Tanner 2009             
21 1329        deGrace 1976            
22 1322        Messer 2016             
23 1259        Vasiliauskas 2013       
24 1225        Nolan 2020              
25 1159        Dorais 2021             
26  361        Toole 2016              
27  122        Schulte-Frankenfeld 2021
   Title                                                                                                                                                                                            
1  Stress and Anxiety Management in Nursing Students: Biofeedback and Mindfulness Meditation                                                                                                        
2  Self-perceived stress of undergraduate students before and after participation in a breathing meditation intervention: A mixed methods study                                                     
3  A randomized controlled trial on effects of the Transcendental Meditation program on blood pressure, psychological distress, and coping in young adults                                          
4  A randomized controlled trial of the effects of mindfulness practice on doctoral candidate psychological status                                                                                  
5  A randomized controlled trial of the effects of brief mindfulness meditation on anxiety symptoms and systolic blood pressure in Chinese nursing students                                         
6  A randomised controlled trial of the effects of mindfulness practice on medical student stress levels                                                                                            
7  Mindfulness meditation's effect on college/university students' mindfulness and transformational leadership                                                                                      
8  Mindfulness in a Graduate Nursing Curriculum: A Randomized Controlled Study                                                                                                                      
9  Meditation and college students' self-actualization and rated stress                                                                                                                             
10 Learning from spiritual models and meditation: A randomized evaluation of a college course                                                                                                       
11 An integrative theory-driven positive emotion regulation intervention                                                                                                                            
12 The influence of a brief mindfulness exercise on encoding of novel words in female college students                                                                                              
13 Impact of App-Delivered Mindfulness Meditation on Functional Connectivity, Mental Health, and Sleep Disturbances Among Physician Assistant Students: Randomized, Wait-list Controlled Pilot Study
14 Gender differences in the benefits of meditation training on attentional blink                                            


### Remove single column names and repeating names with ascending numbers (table headlines)


In [8]:
cols.pop.char <- c()

for (time.point in 0:4){
  cols.pop.char <- append(cols.pop.char,
                          sprintf("Population.Characteristics..Time.Point.%d..",
                                  time.point
                                  )
                          )
}

cols.outc.t <- c()

for (outc in 1:7){
  for (t in 0:3){
    cols.outc.t <- append(cols.outc.t,
                          sprintf("Outcome.%d..Time.Point.%d..",
                                  outc, t
                                  )
                          )
  }
}

cols.quant.results <- c()

for (int.1 in 1:4){
  
}

remove.cols <- c("Dates.of.Measuring.Time.Points.",
                 cols.pop.char[],
                 "Between.Measuring.Time.Points..Duration.",
                 "Intervention.and.Comparisons.",
                 "Definition.of.Outcomes.",
                 "Measures.of.Outcomes.",
                 cols.outc.t[]
                 )

my.df <- my.df[, ! names(my.df) %in% remove.cols]


## Create arrays and data frame lists from Covidence tables


In [9]:
# install.packages("sjmisc")  # for str_contains()
library("sjmisc")


### Set basic parameters


In [10]:
nm.placeholder <- -999  # placeholder for values marked as nm (not mentioned)

flag.x.s.r <- 2
  # x.s.r = exact value (0), mean s (1), or mean r (2)
  # flag.x.s.r = 2 --> include all
  # flag.x.s.r = 1 --> only include mean s and exact values
  # flag.x.s.r = 0 --> include only exact vaules

study.no <- length(my.df[,"Study.ID"])

### Functions

#### Checking for digits and characters

In [11]:
# function returning TRUE if string contains no characters but digits instead
no.char.but.digit.inside <- function(value){
  !(str_contains(value, letters, logic = "OR") |
  str_contains(value, LETTERS, logic = "OR")) &
  grepl("\\d", value)
}

# function returning TRUE if string contains characters
char.inside <- function(value){
  str_contains(value, letters, logic = "OR") |
  str_contains(value, LETTERS, logic = "OR")
}

In [12]:
char.inside("mindfulness meditation")

[1] TRUE


#### For mean values


In [13]:
# extracts mean r and mean s values as double
get.all.means <- function(value){
  if (grepl("mean r", value)){
    extracted.value <- as.double(sub(" mean r.*", "", value))
        # extracts anything before " mean r" as double                 
  } else if (grepl("mean s", value)){
    extracted.value <- as.double(sub(" mean s.*", "", value))
  } else if (grepl("mean", value)){
    extracted.value <- NA
    cat("value ", value, " not added because mean only")
    cat("\n")
  } else {
    extracted.value <- value
  }
  extracted.value
}

# extracts mean s only as double
get.mean.s.only <- function(value){
    if (grepl("mean s", value)){
    extracted.value <- as.double(sub(" mean s.*", "", value))
  } else if (grepl("mean r", value)){
    extracted.value <- NA
    cat("value ", value, " not added because mean r")
    cat("\n")
  } else if (grepl("mean", value)){
    extracted.value <- NA
    cat("value ", value, " not added because mean only")
    cat("\n")
  } else {
    extracted.value <- value
  }
  extracted.value
}


#### Convert value from nm, NA, digit, or char


In [14]:
convert.value <- function(value, nm.placeholder, only.double = TRUE){
  na.value <- FALSE
  if (is.na(value)){
    na.value <- TRUE
  }
  if (na.value == TRUE){
    extracted.value <- NA
  } else {
    value <- as.character(value)
    if (value == "nm"){
      extracted.value <- nm.placeholder
    } else if (value == ""){
      extracted.value <- NA
    } else if (value == "^"){
      extracted.value <- value
        # extracts value after "<" as double 
    } else if (grepl("<", value)){
      extracted.value <- as.double(sub(".*<", "", value))
        # extracts value after "<" as double 
    } else if (grepl(">", value)){
      extracted.value <- as.double(sub(".*>", "", value))
    } else if (no.char.but.digit.inside(value)){
      if (grepl("-", value)){
        # like "0 - 40"
        extracted.value <- value
      } else {
        extracted.value <- as.double(value) 
      }
    } else if (char.inside(value)){
      if (flag.x.s.r == 2){
        extracted.value <- get.all.means(value)
      } else if (flag.x.s.r == 1){
        extracted.value <- get.mean.s.only(value)
      } else if ((flag.x.s.r == 0) & !(grepl("mean r", value) | grepl("mean s", value))){
        extracted.value <- NA
        if (grepl("mean", value)){
          cat("value ", value, " not added because mean only")
          cat("\n")
        }
      } else {
        if (only.double == TRUE){
          extracted.value <- NA
          cat("unknown case with char inside: ", value)
          cat("\n")
        } else {
          extracted.value <- value
        }
      }
    } else {
      cat("unknown case: ", value)
      cat("\n")
    }
  }
  extracted.value
}


#### For arrays


In [15]:
clean.and.shape.data.to.array <- function(
  my.df, start, end, dims, dimname.list, nm.placeholder, flag.x.s.r, study.no
  ){
  my.array <- array(rep(NA),
                    dim = dims,
                    dimnames = dimname.list
                    )
  my.data <- my.df %>%
    select(start:end)
  
  if (length(dims) == 6){
    for (study in 1:study.no){
      my.data.col.no = 1
      for (dim.4.elmnt in 1:dims[4]){
        for (mtrx in 1:dims[3]){
          for (row in 1:dims[1]){
            for (col in 1:dims[2]){
              value <- my.data[study, my.data.col.no]
              my.data.col.no <- my.data.col.no + 1
              if (grepl(",", value)){
                value.before.comma <- sub(",.*", "", value)
                  # extracts anything before "," as double
                my.array[row, col, mtrx, dim.4.elmnt, 1, study] <- convert.value(
                  value.before.comma, nm.placeholder
                  )
                value.after.comma <- sub(".*,", "", value)
                  # extracts anything after "," as double
                my.array[row, col, mtrx, dim.4.elmnt, 2, study] <- convert.value(
                  value.after.comma, nm.placeholder
                  )
              } else {
                my.array[row, col, mtrx, dim.4.elmnt, 1, study] <- convert.value(
                  value, nm.placeholder
                  )
              }
            }
          }
        }
      }
    }
  } else if (length(dims) == 5){
    for (study in 1:study.no){
      my.data.col.no = 1
      for (mtrx in 1:dims[3]){
        for (row in 1:dims[1]){
          for (col in 1:dims[2]){
            value <- my.data[study, my.data.col.no]
            my.data.col.no <- my.data.col.no + 1
            if (grepl(",", value)){
              value.before.comma <- (sub(",.*", "", value))
                # extracts anything before "," as double
              my.array[row, col, mtrx, 1, study] <- convert.value(
                value.before.comma, nm.placeholder
                )
              value.after.comma <- (sub(".*,", "", value))
                # extracts anything after "," as double
              my.array[row, col, mtrx, 2, study] <- convert.value(
                value.after.comma, nm.placeholder
                )
            } else {
              my.array[row, col, mtrx, 1, study] <- convert.value(
                value, nm.placeholder
                )
            }
          }
        }
      }
    }
  } else if (length(dims) <= 4){
    print("too low dim, use function for data frame")
  }
  my.array
}


#### For data frame lists


In [16]:
# create data frames out of 2D Tables (with rows and cols swapped)
clean.data.to.df.list.swap <- function(
  my.df, start, end, dims, list.names, dimname.list
  ){
  study.df <- data.frame(matrix(
    rep(NA),
    nrow = dims[1],
    ncol = dims[2]
  ))
  row.names(study.df) <- dimname.list[[1]]
  colnames(study.df) <- dimname.list[[2]]
  
  # create list of NA data frames of preferred shape
  study.df.list <- list()
  for (i in 1:length(list.names)){
    study.df.list <- append(study.df.list, list(study.df), 0)
  }
  names(study.df.list) <- list.names
  
  my.data <- my.df %>%
    select(start:end)
  
  # vector of my.data.col.no to swapped rows and cols of Covidence output
  my.data.col.no.swapped <- c()
  i <- 0
  j <- 1
  for (k in 1:dims[1]){
    i <- 0
    for (l in 1:dims[2]){
      my.data.col.no.swapped <- append(my.data.col.no.swapped, i * dims[1] + j)
      i <- i + 1
    }
    j <- j + 1 
  }
  # dims[1] = rows new, cols old
  # dims[2] = cols new, rows old
  
  # e.g., filling pattern for old 4 x 7 and new 7 x 4 data frame 
  ## 1, dims[1]+1, 2*dims[1]+1, 3*dims[1]+1, 4*dims[1]+1, 5*dims[1]+1, 6*dims[1]+1,
  ## 2, dims[1]+2, 2*dims[1]+2, 3*dims[1]+2, 4*dims[1]+2, 5*dims[1]+2, 6*dims[1]+2,
  ## x, x, x, x, x, x, x,
  ## x, x, x, x, x, x, x
  
  for (study in 1:study.no){
    m <- 1
    for (row in 1:dims[1]){
      for (col in 1:dims[2]){
        value <- my.data[study, my.data.col.no.swapped[m]]
        m <- m + 1
        study.df.list[[study]][row, col] <- convert.value(
          value, nm.placeholder, only.double = FALSE
          )
      }
    }
  }
  study.df.list
}


In [17]:
# create data frames out of 2D Tables
clean.data.to.df.list <- function(
  my.df, start, end, dims, list.names, dimname.list
  ){
  study.df <- data.frame(matrix(
    rep(NA),
    nrow = dims[1],
    ncol = dims[2]
  ))
  row.names(study.df) <- dimname.list[[1]]
  colnames(study.df) <- dimname.list[[2]]
  
  # create list of NA data frames of preferred shape
  study.df.list <- list()
  for (i in 1:length(list.names)){
    study.df.list <- append(study.df.list, list(study.df), 0)
  }
  names(study.df.list) <- list.names
  
  my.data <- my.df %>%
    select(start:end)
  
  for (study in 1:study.no){
    my.data.col.no <- 1
    for (row in 1:dims[1]){
      for (col in 1:dims[2]){
        value <- my.data[study, my.data.col.no]
        my.data.col.no <- my.data.col.no + 1
        study.df.list[[study]][row, col] <- convert.value(
          value, nm.placeholder, only.double = FALSE
          )
      }
    }
  }
  study.df.list
}


### Arrays


#### means.SDs

In [18]:
dims <- c(4, 3, 4, 7, 2, study.no)

dimname.list <- list(c("Intervention.1", "Intervention.2", "Intervention.3", "Control"),
                     c("Mean", "SD", "n"),
                     c("T0", "T1", "T2", "T3"),
                     c("Outcome.1", "Outcome.2", "Outcome.3", "Outcome.4", "Outcome.5", "Outcome.6", "Outcome.7"),
                     c("Scale.1", "Scale.2"),
                     my.df[,"Study.ID"])

start <- "Intervention.1.Mean.O1T0"
end <- "Control.or.Intervention.4.n.in.case.of.period.O7T3"

means.SDs.array <- clean.and.shape.data.to.array(
    my.df, start, end, dims, dimname.list, nm.placeholder, flag.x.s.r, study.no
) 


Note: Using an external vector in selections is ambiguous.
ℹ Use `all_of(start)` instead of `start` to silence this message.
ℹ See <https://tidyselect.r-lib.org/reference/faq-external-vector.html>.
This message is displayed once per session.
Note: Using an external vector in selections is ambiguous.
ℹ Use `all_of(end)` instead of `end` to silence this message.
ℹ See <https://tidyselect.r-lib.org/reference/faq-external-vector.html>.
This message is displayed once per session.


In [19]:
# use my.pop.char.array[,,"T0","Johnson-Waddell 2018"] as test for "", NA, "nm", "double"
#      [,1]  [,2] [,3] [,4]  [,5]
# [1,] "197" NA   NA   "197" 394 
# [2,] ""    ""   NA   ""    "nm"
# [3,] ""    NA   NA   ""    "nm"
# [4,] ""    NA   NA   ""    "" 
# make flag.x.s.r work --> done


In [30]:
means.SDs.array

, , T0, Outcome.1, Scale.1, Ratanasiripong 2015

                Mean   SD  n
Intervention.1    NA   NA NA
Intervention.2 17.24 4.16 NA
Intervention.3    NA   NA NA
Control        17.29 3.50 NA

, , T1, Outcome.1, Scale.1, Ratanasiripong 2015

               Mean    SD    n
Intervention.1   NA    NA   NA
Intervention.2   NA 14.90 3.44
Intervention.3   NA    NA   NA
Control          NA 16.74 4.71

, , T2, Outcome.1, Scale.1, Ratanasiripong 2015

               Mean SD  n
Intervention.1   NA NA NA
Intervention.2   NA NA NA
Intervention.3   NA NA NA
Control          NA NA NA

, , T3, Outcome.1, Scale.1, Ratanasiripong 2015

               Mean SD  n
Intervention.1   NA NA NA
Intervention.2   NA NA NA
Intervention.3   NA NA NA
Control          NA NA NA

, , T0, Outcome.2, Scale.1, Ratanasiripong 2015

               Mean    SD   n
Intervention.1   NA    NA  NA
Intervention.2   NA    NA  NA
Intervention.3   NA 25.45 7.8
Control          NA    NA  NA

, , T1, Outcome.2, Scale.1, Ratanasiripong 2015

               Mean    SD     n
Intervention.1   NA 23.74  7.72
Intervention.2   NA    NA 21.28
Intervention.3 6.95    NA    NA
Control          NA    NA    NA

, , T2, Outcome.2, Scale.1, Ratanasiripong 2015

               Mean SD     n
Intervention.1   NA NA 24.74
Intervention.2 9.91 NA    NA
Intervention.3   NA NA    NA
Control          NA NA    NA

, , T3, Outcome.2, Scale.1, Ratanasiripong 2015

               Mean SD  n
Intervention.1   NA NA NA
Intervention.2   NA NA NA
Intervention.3   NA NA NA
Control          NA NA NA

, , T0, Outcome.3, Scale.1, Ratanasiripong 2015

               Mean SD  n
Intervention.1   NA NA NA
Intervention.2   NA NA NA
Intervention.3   NA NA NA
Control          NA NA NA

, , T1, Outcome.3, Scale.1, Ratanasiripong 2015

               Mean SD  n
Intervention.1   NA NA NA
Intervention.2   NA NA NA
Intervention.3   NA NA NA
Control          NA NA NA

, , T2, Outcome.3, Scale.1, Ratanasiripong 2015

               Mean SD  n
Intervention.1   NA NA NA
Intervention.2   NA NA NA
Intervention.3   NA NA NA
Control          NA NA NA

, , T3, Outcome.3, Scale.1, Ratanasiripong 2015

               Mean SD  n
Intervention.1   NA NA NA
Intervention.2   NA NA NA
Intervention.3   NA NA NA
Control          NA NA NA

, , T0, Outcome.4, Scale.1, Ratanasiripong 2015

               Mean SD  n
Intervention.1   NA NA NA
Intervention.2   NA NA NA
Intervention.3   NA NA NA
Control          NA NA NA

, , T1, Outcome.4, Scale.1, Ratanasiripong 2015

               Mean SD  n
Intervention.1   NA NA NA
Intervention.2   NA NA NA
Intervention.3   NA NA NA
Control          NA NA NA

, , T2, Outcome.4, Scale.1, Ratanasiripong 2015

               Mean SD  n
Intervention.1   NA NA NA
Intervention.2   NA NA NA
Intervention.3   NA NA NA
Control          NA NA NA

, , T3, Outcome.4, Scale.1, Ratanasiripong 2015

               Mean SD  n
Intervention.1   NA NA NA
Intervention.2   NA NA NA
Intervention.3   NA NA NA
Control          NA NA NA

, , T0, Outcome.5, Scale.1, Ratanasiripong 2015

               Mean SD  n
Intervention.1   NA NA NA
Intervention.2   NA NA NA
Intervention.3   NA NA NA
Control          NA NA NA

, , T1, Outcome.5, Scale.1, Ratanasiripong 2015

               Mean SD  n
Intervention.1   NA NA NA
Intervention.2   NA NA NA
Intervention.3   NA NA NA
Control          NA NA NA

, , T2, Outcome.5, Scale.1, Ratanasiripong 2015

               Mean SD  n
Intervention.1   NA NA NA
Intervention.2   NA NA NA
Intervention.3   NA NA NA
Control          NA NA NA

, , T3, Outcome.5, Scale.1, Ratanasiripong 2015

               Mean SD  n
Intervention.1   NA NA NA
Intervention.2   NA NA NA
Intervention.3   NA NA NA
Control          NA NA NA

, , T0, Outcome.6, Scale.1, Ratanasiripong 2015

               Mean SD  n
Intervention.1   NA NA NA
Intervention.2   NA NA NA
Intervention.3   NA NA NA
Control          NA NA NA

, , T1, Outcome.6, Scale.1, Ratanasiripong 2015

               Mean SD  n
Intervention.1   NA NA NA
Intervention.2


#### Results Quantitative


In [20]:
dims <- c(7, 3, 3, 6, 2, study.no)

dimname.list <- list(c("Outcome.1", "Outcome.2", "Outcome.3", "Outcome.4", "Outcome.5", "Outcome.6", "Outcome.7"),
                     c("P.Value", "Effect.Size", "Effect.Size.CI"),
                     c("T1", "T2", "T3"),
                     c("Int1.X.Int2", "Int1.X.Int3", "Int1.X.Int4", "Int2.X.Int3", "Int2.X.Int4", "Int3.X.Int4"),
                     c("Scale.1", "Scale.2"),
                     my.df[,"Study.ID"]
                     )

start <- "Outcome.1.P.Value.1x2T1"
end <- "Outcome.7.Confidence.Interval.of.Effect.Size.3x4T3"

results.quantitative.array <- clean.and.shape.data.to.array(
    my.df, start, end, dims, dimname.list, nm.placeholder, flag.x.s.r, study.no
)


### Data frame lists

#### Intervention Comparison

In [21]:
dims <- c(4, 7)

list.names <- my.df[,"Study.ID"]

dimname.list <- list(c("Intervention.1", "Intervention.2", "Intervention.3", "Control"),
                     c("Name", "Short.Description", "Delivery.Mode", "Meditation.App", "Sessions.Duration.in.minutes",
                       "Frequency.in.times.per.week", "Total.Duration.in.Days")
                     )
start <- "Name.Intervention.1"
end <- "Total.Duration.of.Intervention.in.Days.Control.or.Intervention.4"

intervention.comparisons.df.list <- clean.data.to.df.list.swap(
 my.df, start, end, dims, list.names, dimname.list
)
intervention.comparisons.df.list


value  0.99 mean  not added because mean only
value  36.67 mean  not added because mean only
value  3.79 during intervention, 2.04 during follow-up mean  not added because mean only
value  4.19 mean  not added because mean only
value  12.5 mean  not added because mean only
value  2.5 mean  not added because mean only
value  11.19 mean  not added because mean only
value  2.82 mean  not added because mean only


$`Ratanasiripong 2015`
                                 Name Short.Description Delivery.Mode
Intervention.1                   <NA>                NA            NA
Intervention.2 mindfulness meditation                NA            NA
Intervention.3                   <NA>                NA            NA
Control               no intervention                NA            NA
               Meditation.App Sessions.Duration.in.minutes
Intervention.1             NA                           NA
Intervention.2             NA                           NA
Intervention.3             NA                           NA
Control                    NA                           NA
               Frequency.in.times.per.week Total.Duration.in.Days
Intervention.1                          NA                     NA
Intervention.2                          NA                     NA
Intervention.3                          NA                     NA
Control                                 NA                     NA

$`Sloan 2016`
                               Name
Intervention.1 breathing meditation
Intervention.2                 <NA>
Intervention.3                 <NA>
Control             no intervention
                                          Short.Description
Intervention.1 "guided audio-recorded breathing meditation"
Intervention.2                                         <NA>
Intervention.3                                         <NA>
Control                                                <NA>
                                                                      Delivery.Mode
Intervention.1 Asynchronous guiding by a recorded voice (e.g. App), audio recording
Intervention.2                                                                 <NA>
Intervention.3                                                                 <NA>
Control                                                                        <NA>
               Meditation.App Sessions.Duration.in.minutes
Intervention.1             NA                            9
Intervention.2             NA                           NA
Intervention.3             NA                           NA
Control                    NA                           NA
               Frequency.in.times.per.week Total.Duration.in.Days
Intervention.1                          NA                     56
Intervention.2                          NA                     NA
Intervention.3                          NA                     NA
Control                                 NA                     NA

$`Nidich 2009`
                                          Name
Intervention.1  Transcendental meditation (TM)
Intervention.2                            <NA>
Intervention.3                            <NA>
Control                      wait-list control
                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      Short.Description
Intervention.1 "The TM technique [...] that allows the\nordinary thinking process to become more quiescent and a\nunique psychophysiologic state of “restful alertness” to be\ngained.28 This distinctive state of restful alertnes


#### Dates of Measuring Time Points


In [22]:
dims <- c(4, 1)

list.names <- my.df[,"Study.ID"]

dimname.list <- list(c("Time.Point.0", "Time.Point.1", "Time.Point.2", "Time.Point.3"),
                     c("Date")
                     )
start <- "Time.Point.0.Date"
end <- "Time.Point.3.Date"

dates.measuring.time.points.df.list <- clean.data.to.df.list(
 my.df, start, end, dims, list.names, dimname.list
)
dates.measuring.time.points.df.list


$`Ratanasiripong 2015`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA

$`Sloan 2016`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA

$`Nidich 2009`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA

$`Barry 2019`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA

$`Chen 2013`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA

$`Warnecke 2011`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA

$`Johnson-Waddell 2018`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA

$`Plummer 2018`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA

$`Janowiak 1994`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA

$`Oman 2007`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA

$`Weytens 2014`
                                       Date
Time.Point.0 1 week before the intervention
Time.Point.1 2 weeks after the intervention
Time.Point.2                           <NA>
Time.Point.3                           <NA>

$`Bonamo 2015`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA

$`Smith 2021`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA

$`Wang 2021`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA

$`Fish 2019`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA

$`Siembor 2018`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA

$`Lee 2018`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA

$`Bultas 2021`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA

$`Huberty 2019`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA

$`Tanner 2009`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA

$`deGrace 1976`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA

$`Messer 2016`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA

$`Vasiliauskas 2013`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA

$`Nolan 2020`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA

$`Dorais 2021`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA

$`Toole 2016`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA

$`Schulte-Frankenfeld 2021`
             Date
Time.Point.0   NA
Time.Point.1   NA
Time.Point.2   NA
Time.Point.3   NA


#### Between-Measuring Time Points Duration


In [23]:
dims <- c(3, 1)

list.names <- my.df[,"Study.ID"]

dimname.list <- list(c("Time.Point.0...1", "Time.Point.0...2", "Time.Point.0...3"),
                     c("Duration.in.Days")
                     )
start <- "Time.Point.0...1.Duration.in.Days"
end <- "Time.Point.0...3.Duration.in.Days"

between.T.duration.df.list <- clean.data.to.df.list(
 my.df, start, end, dims, list.names, dimname.list
)
between.T.duration.df.list


value  7 mean  not added because mean only


$`Ratanasiripong 2015`
                 Duration.in.Days
Time.Point.0...1               28
Time.Point.0...2               NA
Time.Point.0...3               NA

$`Sloan 2016`
                 Duration.in.Days
Time.Point.0...1               NA
Time.Point.0...2               NA
Time.Point.0...3               NA

$`Nidich 2009`
                 Duration.in.Days
Time.Point.0...1               90
Time.Point.0...2               NA
Time.Point.0...3               NA

$`Barry 2019`
                 Duration.in.Days
Time.Point.0...1               NA
Time.Point.0...2               NA
Time.Point.0...3               NA

$`Chen 2013`
                 Duration.in.Days
Time.Point.0...1                6
Time.Point.0...2               NA
Time.Point.0...3               NA

$`Warnecke 2011`
                 Duration.in.Days
Time.Point.0...1               56
Time.Point.0...2              112
Time.Point.0...3               NA

$`Johnson-Waddell 2018`
                 Duration.in.Days
Time.Point.0...1             45.5
Time.Point.0...2               NA
Time.Point.0...3               NA

$`Plummer 2018`
                 Duration.in.Days
Time.Point.0...1               70
Time.Point.0...2              140
Time.Point.0...3              224

$`Janowiak 1994`
                 Duration.in.Days
Time.Point.0...1               NA
Time.Point.0...2               NA
Time.Point.0...3               NA

$`Oman 2007`
                 Duration.in.Days
Time.Point.0...1               56
Time.Point.0...2              112
Time.Point.0...3               NA

$`Weytens 2014`
                 Duration.in.Days
Time.Point.0...1               NA
Time.Point.0...2               NA
Time.Point.0...3               NA

$`Bonamo 2015`
                 Duration.in.Days
Time.Point.0...1                0
Time.Point.0...2               NA
Time.Point.0...3               NA

$`Smith 2021`
                 Duration.in.Days
Time.Point.0...1               56
Time.Point.0...2               NA
Time.Point.0...3               NA

$`Wang 2021`
                 Duration.in.Days
Time.Point.0...1               NA
Time.Point.0...2               NA
Time.Point.0...3               NA

$`Fish 2019`
                 Duration.in.Days
Time.Point.0...1               NA
Time.Point.0...2               NA
Time.Point.0...3               NA

$`Siembor 2018`
                 Duration.in.Days
Time.Point.0...1               NA
Time.Point.0...2               NA
Time.Point.0...3               NA

$`Lee 2018`
                 Duration.in.Days
Time.Point.0...1               28
Time.Point.0...2               NA
Time.Point.0...3               NA

$`Bultas 2021`
                 Duration.in.Days
Time.Point.0...1               NA
Time.Point.0...2               NA
Time.Point.0...3               NA

$`Huberty 2019`
                 Duration.in.Days
Time.Point.0...1               56
Time.Point.0...2               84
Time.Point.0...3               NA

$`Tanner 2009`
                 Duration.in.Days
Time.Point.0...1            91.25
Time.Point.0...2               NA
Time.Point.0...3               NA

$`deGrace 1976`
                 Duration.in.Days
Time.Point.0...1               NA
Time.Point.0...2               NA
Time.Point.0...3               NA

$`Messer 2016`
                 Duration.in.Days
Time.Point.0...1               NA
Time.Point.0...2               NA
Time.Point.0...3               NA

$`Vasiliauskas 2013`
                 Duration.in.Days
Time.Point.0...1               21
Time.Point.0...2               NA
Time.Point.0...3               NA

$`Nolan 2020`
                 Duration.in.Days
Time.Point.0...1               NA
Time.Point.0...2               NA
Time.Point.0...3               NA

$`Dorais 2021`
                 Duration.in.Days
Time.Point.0...1               13
Time.Point.0...2               27
Time.Point.0...3               NA

$`Toole 2016`
                 Duration.in.Days
Time.Point.0...1               NA
Time.Point.0...2               NA
Time.Point.0...3               NA

$`Schulte-Frankenfeld 2021`
    


#### Definition of Outcomes


In [24]:
dims <- c(7, 1)

list.names <- my.df[,"Study.ID"]

dimname.list <- list(c("Outcome.1", "Outcome.2", "Outcome.3", "Outcome.4", "Outcome.5", "Outcome.6", "Outcome.7"),
                     c("Definition")
                     )
start <- "Outcome.1.Definition"
end <- "Outcome.7.Definition"

outcome.definitions.df.list <- clean.data.to.df.list(
 my.df, start, end, dims, list.names, dimname.list
)
outcome.definitions.df.list


$`Ratanasiripong 2015`
                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       Definition
Outcome.1                                                                                                                                                                                                                                                                                                                      "Lazarus and Folkman (1984) asserted that a psychological\nexperience of stress results when a situation is perceived to be\nharmful or exceeding one’s resources"
Outcome.2 "Anxiety can be seen as\nrelatively related to stress, in that it can be aggravated by the\npresence of prolonged stress and multiple stressors. Anxiety is\na state of apprehension and an out-of-proportion response to a\nperceived threat, which can disrupt psychological functioning\nand manifest as physiological symptoms, such as elevated blood\npressure, sweating, dizziness, or increased heartbeat (Editors of\nthe American Heritage Dictionaries, 2007; Lewis, 1970)."
Outcome.3                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    <NA>
Outcome.4                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    <NA>
Outcome.5                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    <NA>
Outcome.6                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    <NA>
Outcome.7                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    <NA>

$`Sloan 2016`
                                                                                                          


#### Measures of Outcomes


In [25]:
dims <- c(7, 3)

list.names <- my.df[,"Study.ID"]

dimname.list <- list(c("Outcome.1", "Outcome.2", "Outcome.3", "Outcome.4", "Outcome.5", "Outcome.6", "Outcome.7"),
                     c("Measures.Name", "Start.and.End.Point", "High.or.low.means.resilient")
                     )
start <- "Outcome.1.Scale.s.or.other.Measure.s.Name"
end <- "Outcome.7.High.or.low.means.resilient"

outcome.measures.df.list <- clean.data.to.df.list(
 my.df, start, end, dims, list.names, dimname.list
)
outcome.measures.df.list


$`Ratanasiripong 2015`
                                                                                                             Measures.Name
Outcome.1                                                Perceived Stress Scale (PSS; Cohen, Kamarck, & Mermelstein, 1983)
Outcome.2 State Anxiety Scale from the State–Trait Anxiety Inventory (Spielberger, Gorsuch, Lushene, Vagg, & Jacobs, 1983)
Outcome.3                                                                                                             <NA>
Outcome.4                                                                                                             <NA>
Outcome.5                                                                                                             <NA>
Outcome.6                                                                                                             <NA>
Outcome.7                                                                                                             <NA>
          Start.and.End.Point High.or.low.means.resilient
Outcome.1                -999                        -999
Outcome.2                  NA                          NA
Outcome.3                  NA                          NA
Outcome.4                  NA                          NA
Outcome.5                  NA                          NA
Outcome.6                  NA                          NA
Outcome.7                  NA                          NA

$`Sloan 2016`
                             Measures.Name Start.and.End.Point
Outcome.1 The Perceived Stress Scale (PSS)              0 - 40
Outcome.2                             <NA>                <NA>
Outcome.3                             <NA>                <NA>
Outcome.4                             <NA>                <NA>
Outcome.5                             <NA>                <NA>
Outcome.6                             <NA>                <NA>
Outcome.7                             <NA>                <NA>
          High.or.low.means.resilient
Outcome.1                           v
Outcome.2                        <NA>
Outcome.3                        <NA>
Outcome.4                        <NA>
Outcome.5                        <NA>
Outcome.6                        <NA>
Outcome.7                        <NA>

$`Nidich 2009`
                                                        Measures.Name
Outcome.1 Profile of Mood States total mood disturbance main scale 23
Outcome.2                     Profile of Mood States anxiety subscale
Outcome.3                  Profile of Mood States depression subscale
Outcome.4                                                        <NA>
Outcome.5                                                        <NA>
Outcome.6                                                        <NA>
Outcome.7                                                        <NA>
          Start.and.End.Point High.or.low.means.resilient
Outcome.1                -999                        -999
Outcome.2                -999                        -999
Outcome.3                -999                        -999
Outcome.4                  NA                          NA
Outcome.5                  NA                          NA
Outcome.6                  NA                          NA
Outcome.7                  NA                          NA

$`Barry 2019`
                                                                                Measures.Name
Outcome.1                                     Depression, Anxiety\nand Stress Scale (DASS) 26
Outcome.2                                     Depression, Anxiety\nand Stress Scale (DASS) 26
Outcome.3 Depression, Anxiety\nand Stress Scale (DASS) 26, Perceived Stress Scale\n(PSS)27,28
Outcome.4                                       Psychological Capital\nQuestionnaire (PCQ) 19
Outcome.5                                       Psychological Capital\nQuestionnaire (PCQ) 19
Outcome.6                                       Psychological Capital\nQuestionnaire (P


#### Qualitative Results of Data Analyses


In [26]:
dims <- c(7, 3)

list.names <- my.df[,"Study.ID"]

dimname.list <- list(c("Key.Theme.1", "Key.Theme.2", "Key.Theme.3", "Key.Theme.4", "Key.Theme.5", "Key.Theme.6", "Key.Theme.7"),
                     c("Name.of.Key.Theme", "Description.of.Key.Theme", "Results")
                     )
start <- "Key.Theme.1.Name.of.Key.Theme"
end <- "Key.Theme.7.Results"

results.qualitative.df.list <- clean.data.to.df.list(
 my.df, start, end, dims, list.names, dimname.list
)
results.qualitative.df.list


$`Ratanasiripong 2015`
            Name.of.Key.Theme Description.of.Key.Theme Results
Key.Theme.1                NA                       NA      NA
Key.Theme.2                NA                       NA      NA
Key.Theme.3                NA                       NA      NA
Key.Theme.4                NA                       NA      NA
Key.Theme.5                NA                       NA      NA
Key.Theme.6                NA                       NA      NA
Key.Theme.7                NA                       NA      NA

$`Sloan 2016`
                      Name.of.Key.Theme Description.of.Key.Theme Results
Key.Theme.1 See "Table 18. Major Codes"                       NA      NA
Key.Theme.2                        <NA>                       NA      NA
Key.Theme.3                        <NA>                       NA      NA
Key.Theme.4                        <NA>                       NA      NA
Key.Theme.5                        <NA>                       NA      NA
Key.Theme.6                        <NA>                       NA      NA
Key.Theme.7                        <NA>                       NA      NA

$`Nidich 2009`
            Name.of.Key.Theme Description.of.Key.Theme Results
Key.Theme.1                NA                       NA      NA
Key.Theme.2                NA                       NA      NA
Key.Theme.3                NA                       NA      NA
Key.Theme.4                NA                       NA      NA
Key.Theme.5                NA                       NA      NA
Key.Theme.6                NA                       NA      NA
Key.Theme.7                NA                       NA      NA

$`Barry 2019`
                                      Name.of.Key.Theme
Key.Theme.1    Self-reported stress during trial period
Key.Theme.2 Self-Stress-Management during\ntrial period
Key.Theme.3                                        <NA>
Key.Theme.4                                        <NA>
Key.Theme.5                                        <NA>
Key.Theme.6                                        <NA>
Key.Theme.7                                        <NA>
                                                                                                                                                                                                                                   Description.of.Key.Theme
Key.Theme.1                                                                                                                                                   Question: "Did you experience any stress related to your\nPhD during the last 8-week period?"
Key.Theme.2 Question: "Did you undertake or receive any other support\nwith the aim to reduce stress related to your PhD during the last 8-week period? If so, please describe below and outline whether this helped you to cope\nwith your stress levels."
Key.Theme.3                                                                                                                                                                                                                                            <NA>
Key.Theme.4                                                                                                                                                                                                                                            <NA>
Key.Theme.5                                                                                                                                                                                                                                            <NA>
Key.Theme.6                                                                                                                                                                                                                                            <NA>
Key.Theme.7                                                                                                                    

### Data frame of left 1D Data

## Put total data into a list

In [ ]:
m.data.list <- list(
    
)

# Notes

- Different Scales
    - 2 Array-Dims with same values
    - Results in Dim "Scale.2" only if 2nd scale is present, else: NA

# ToDo

- find solution for value: '3.79 during intervention, 2.04 during follow-up mean'
- find a way to combine 1st measures name with Scales name in results
- put total data into a list

# Array Dims and Dimnames

Dates of Measuring Time Points
	4 x 1
	c("Time.Point.0", "Time.Point.1", "Time.Point.2", "Time.Point.3")
	c("Date")
	Time.Point.0.Date:Time.Point.3.Date
	
Between-Measuring Time Points' Duration
	3 x 1
	c("Time.Point.0...1", "Time.Point.0...2", "Time.Point.0...3")
	c("Duration.in.Days")
	Time.Point.0...1:Duration.in.Days

Intervention and Comparisons
	7 x 4
	c("Name", "Short.Description", "Delivery.Mode", "Meditation.App", "Sessions.Duration.in.minutes", Frequency.in.times.per.week", "Total.Duration.in.Days")
	c("Intervention.1", "Intervention.2", "Intervention.3", "Control")
	Name.Intervention 1:Total.Duration.of.Intervention.in.Days.Control.or.Intervention.4

Definition of Outcomes
	7 x 1
	c("Outcome.1", "Outcome.2", "Outcome.3", "Outcome.4", "Outcome.5", "Outcome.6", "Outcome.7")
	c("Definition")
	Outcome.1:Definition

Measures of Outcomes
	7 x 3
	c("Outcome.1", "Outcome.2", "Outcome.3", "Outcome.4", "Outcome.5", "Outcome.6", "Outcome.7")
	c("Measures.Name", "Start.and.End.Point", "High.or.low.means.resilient")
	Outcome.1.Scale.s.or.other.Measure.s.Name:Outcome.7.High.or.low.means.resilient
	
Means and SDs of Outcomes
	4 x 3 x 4 x 7
	c("Intervention.1", "Intervention.2", "Intervention.3", "Control"
	c("Mean", "SD", "n")
	c("T0", "T1", "T2", "T3")
	c("Outcome.1", "Outcome.2", "Outcome.3", "Outcome.4", "Outcome.5", "Outcome.6", "Outcome.7")
	Intervention.1.Mean.O1T0:Control.or.Intervention.4.n.in.case.of.period.O7T3

Quantitative Results of Data Analyses
	7 x 3 x 3 x 6
	c("Outcome.1", "Outcome.2", "Outcome.3", "Outcome.4", "Outcome.5", "Outcome.6", "Outcome.7")
	c("P.Value", "Effect.Size", "Effect.Size.CI")
	c("T1", "T2", "T3")
	c("Int1.X.Int2", "Int1.X.Int3", "Int1.X.Int4", "Int2.X.Int3", "Int2.X.Int4", "Int3.X.Int4")
	Outcome.1.P.Value.1x2T1:Outcome.7.Confidence.Interval.of.Effect.Size.3x4T3

Qualitative Results of Data Analyses
	7 x 3
	c("Key.Theme.1", "Key.Theme.2", "Key.Theme.4", "Key.Theme.5", "Key.Theme.6", "Key.Theme.7")
	c("Name.of.Key.Theme", "Description.of.Key.Theme", "Results")
	Key.Theme.1:Results